In [ ]:
#CELL 1
#@title Keep this tab alive to prevent Colab from disconnecting you { display-mode: "form" }
#@markdown Press play on the music player that will appear below:
%%html
<audio src="https://oobabooga.github.io/silence.m4a" controls>


In [ ]:
#@title ##**Start TextGenWebUI**
#GOOGLE COLAB ONLY
import os, signal, fileinput
from IPython.utils import capture

# Find any existing cloudflared processes
result = os.popen('ps -A | grep cloudflared').read()
if 'cloudflared' in result:
    # If a cloudflared process is found, kill it
    os.kill(int(result.split()[0]), signal.SIGKILL)

#@markdown ####**Configure and Run**
text_streaming = False #@param {type:"boolean"}
GetAPI = True #@param {type:"boolean"}

#Parameters
huggingface_org="Kotokin" #@param{type:"string"}
huggingface_repo="MLewd-L2-13B-v2-1-GPTQ" #@param{type:"string"}
model = huggingface_repo
huggingface_branch="main" #@param{type:"string"}

load_in_8bit = False
load_in_4bit = True
if ('GPTQ' in model or '4bit' in model or '128' in huggingface_repo):
    load_in_8bit = False
    load_in_4bit = True

##### Oobabooga ######
#Main Directories:
main_dir = "/content/text-generation-webui/"
cache = f"{main_dir}cache"

def patch_file(filename, search_str, replace_str):
    with fileinput.FileInput(filename, inplace=True) as f:
        for line in f:
            if search_str in line:
                line = line.replace(search_str, replace_str)
            print(line, end='')

def install_ooba(): #$
  %cd /content
  !apt-get -y install -qq aria2
  !mkdir {main_dir}cache
  !mkdir text-generation-webui/logs
  !ln -s text-generation-webui/logs .
  !ln -s text-generation-webui/characters .
  !ln -s text-generation-webui/models .
  !rm -r sample_data

  %cd {main_dir}
  !wget https://oobabooga.github.io/settings-colab.json
  !rm -rf /content/text-generation-webui/presets/Default.txt /content/text-generation-webui/settings-colab-template.json /content/text-generation-webui/settings-template.json

  link="https://huggingface.co/Imablank/AnythingV3-1/raw/main/GPT4.txt, https://huggingface.co/Imablank/AnythingV3-1/raw/main/Alpha.json, https://huggingface.co/Imablank/AnythingV3-1/resolve/main/Alpha.png, https://huggingface.co/Imablank/AnythingV3-1/raw/main/settings.json"
  path="/content/text-generation-webui/presets/, /content/characters/, /content/characters/, /content/text-generation-webui/"
  nan3="GPT4.txt, Alpha.json, Alpha.png, settings.json"; link=link.split(', '); path=path.split(', '); nan3=nan3.split(', ')
  for link, path, nan3 in zip(link, path, nan3):
    universal_download(link, path, nan3)
  !pip install -r requirements.txt
  !pip install flask-cloudflared websockets

def download_model(huggingface_repobranch, huggingface_org, huggingface_repo, huggingface_branch): #$
  tmp_repo=f"/content/.{huggingface_repo}"
  !git lfs install --skip-smudge && export GIT_LFS_SKIP_SMUDGE=1 && git clone https://huggingface.co/{huggingface_org}/{huggingface_repo} /content/.{huggingface_repo} --branch {huggingface_branch}
  !rm -rf {tmp_repo}/pytorch_model.bin.index.json {tmp_repo}/training_args.bin {tmp_repo}/trainer_state.json {tmp_repo}/all_results.json {tmp_repo}/eval_results.json {tmp_repo}/.gitattributes {tmp_repo}/train_results.json
  repo = os.listdir(tmp_repo);
  for download in repo:
    link_path = f"https://huggingface.co/{huggingface_org}/{huggingface_repo}/"
    if ".json" in download or ".txt" in download:
      link_path += f"raw/{huggingface_branch}/{download}"
    else: link_path += f"resolve/{huggingface_branch}/{download}"
    !aria2c --console-log-level=error -c -x 16 -s 16 -k 1M {link_path} -d /content/text-generation-webui/models/{huggingface_repobranch} -o {download}

def universal_download(link1, path1, nan3):
  !aria2c --console-log-level=error -c -x 16 -s 16 -k 1M {link1} -d {path1} -o {nan3}

print("\033[92m[Installing oobabooga]")
if (not os.path.exists(main_dir) or ('GPTQ' in model or '4bit' in model or '128' in model) and not os.path.exists(f"{main_dir}repositories")):
  %cd /content
  !git clone https://github.com/oobabooga/text-generation-webui/
  # Patch the file
  search_string = 'parser.add_argument(\'--alpha_value\', type=int, default=1, help="Positional embeddings alpha factor for NTK RoPE scaling. Use either this or compress_pos_emb, not both.")'
  replace_string = 'parser.add_argument(\'--alpha_value\', type=float, default=1, help="Positional embeddings alpha factor for NTK RoPE scaling. Use either this or compress_pos_emb, not both.")'
  patch_file("/content/text-generation-webui/modules/shared.py", search_string, replace_string)
  print("Ooba was patched to use NTK with float value...")

with capture.capture_output() as cap:
    install_ooba();
!rm -rf /content/text-generation-webui/models/config.yaml
%cd /content

huggingface_repobranch=""
if not "main" == huggingface_branch: huggingface_repobranch=f"{huggingface_repo}_{huggingface_branch}"
else:huggingface_repobranch=huggingface_repo

print(f"\033[92m[Installing Model {huggingface_repo}]")
if not os.path.exists(f"/content/models/{huggingface_repo}"):
    download_model(huggingface_repobranch, huggingface_org, huggingface_repo, huggingface_branch);

#Server starting
print("\033[92m[Starting Server]")
params = set()
if ('4bit' in model): params.add('--wbits 4 --model_type Llama')
if ('128' in model): params.add('--groupsize 128')
if load_in_8bit: params.add('--load-in-8bit')
if load_in_4bit: params.add('--load-in-4bit')
if GetAPI: params.add('--public-api')
if ('GPTQ' in model):
    params.add("--loader exllama_hf --max_seq_len 7500 --alpha_value 2.565")
else:
    params.add("--loader llamacpp")

active_extensions = []
if GetAPI: active_extensions.append('api')
if len(active_extensions) > 0: params.add(f'--extensions {" ".join(active_extensions)}')
print("\033[1m "+"\033[92m ")

def run_ooba():#$
  %cd {main_dir}
  cmd = f"python server.py --model {huggingface_repobranch} {' '.join(params)}"
  print(cmd)
  !$cmd

filler=" "
if GetAPI:
    print("\033[92m[Running Ooba...]")
    run_ooba()